In [45]:
max_words = 200
max_len = 40
num_classes = 1

# Training
epochs = 20
batch_size = 512
print_batch_n = 100

In [46]:
import pandas as pd

df_train = pd.read_csv("/home/alex/dev/AiLearning/DataSetStore/text_classification_1/train.csv")
df_test = pd.read_csv("/home/alex/dev/AiLearning/DataSetStore/text_classification_1/test.csv")
df_val = pd.read_csv("/home/alex/dev/AiLearning/DataSetStore/text_classification_1/val.csv")

In [47]:
df_train

id                                               text  class
0            0  @alisachachka не уезжаааааааай. :(❤ я тоже не ...      0
1            1  RT @GalyginVadim: Ребята и девчата!\nВсе в кин...      1
2            2  RT @ARTEM_KLYUSHIN: Кто ненавидит пробки ретви...      0
3            3  RT @epupybobv: Хочется котлету по-киевски. Зап...      1
4            4  @KarineKurganova @Yess__Boss босапопа есбоса н...      1
...        ...                                                ...    ...
181462  181462  Классным будет новый год..( http://t.co/LejaGu...      0
181463  181463  Видишь человека хочешь сказать ему привет . А ...      0
181464  181464  @Julia6_9Styles там длинный диагноз. Вкратце: ...      0
181465  181465  @technoslav ух ты, а кому тот серенький кнопоч...      1
181466  181466  @Kris1D_07 я тоже так собираюсь сделать:D наве...      1

[181467 rows x 3 columns]

In [48]:
import re
import nltk
from nltk.tokenize import word_tokenize, wordpunct_tokenize
from nltk import tokenize as tknz
from nltk.corpus import stopwords

from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.corpus import wordnet

nltk.download('wordnet')

# Just copy from the homework of the lesson -1
class MessageCleaner:
    
    def __init__(self,message=None):
        self._message= message
        self.tokens=[]

    def set_message(self,msg):
        self._message = msg;
        return self

    def get_message(self):
        return self._message

    def remove_users(self,replace=" "):
        xtr = re.sub(pattern="@[\w]*",repl=replace,string=self._message)
        self._message = xtr
        return self
    
    def remove_punctuation(self,replace=" "):
        xtr = re.sub(pattern=r'[^\w\s]',repl=replace,string=self._message)
        self._message = xtr
        return self

    def remove_en_special_sym(self,replace=" "):
        xtr = re.sub(pattern=r'[^a-zA-Z0-9]',repl=replace,string=self._message)
        self._message = xtr
        return self

    def remove_ru_special_sym(self,replace=" "):
        xtr = re.sub(pattern=r'[^а-яА-Я0-9]',repl=replace,string=self._message)
        self._message = xtr
        return self
    
    def remove_en_numbers(self,replace=" "):
        xtr = re.sub(pattern=r'[^a-zA-Z]',repl=replace,string=self._message)
        self._message = xtr
        return self

    def remove_ru_numbers(self,replace=" "):
        xtr = re.sub(pattern=r'[^а-яА-Я]',repl=replace,string=self._message)
        self._message = xtr
        return self

    def clean_by_regexp(self,regexp: str):
        pattern = re.compile(regexp)
        xtr = pattern.subn(' ', self._message)[0]
        self._message = xtr
        return self

    def to_lower (self ):
        self._message = self._message.lower();
        return self;

    def replace_by_dicts (self,dictionary: map):
        for key in dictionary:
            self._message = self._message.replace(key,dictionary[key])
            #re.sub(pattern=key,repl=dictionary[key],string=self._message)
        return self

    def escape_single_symbol_words (self):
        self._message=" ".join([word for word in self._message.split() if len(word)>1])
        return self

    def nltk_word_tokenize(self):
        self.tokens=tknz.word_tokenize(self._message)
        return self

    def nltk_word_punc_tokenize(self):
        self.tokens = tknz.wordpunct_tokenize(self._message)
        return self

    def nltk_tok_tok_tokenizer(self):
        self.tokens = tknz.ToktokTokenizer().tokenize(self._message)
        return self
        
    def nltk_tweet_tokenizer(self):
        self.tokens = tknz.TweetTokenizer().tokenize(self._message)
        return self

    def nltk_with_regexp_tokenizer (self,regexp):
        self.tokens = tknz.RegexpTokenizer(regexp).tokenize(self._message)
        return self

    def nltk_sentence_tokenizer (self):
        self.tokens = nltk.sent_tokenize(self._message)
        return self

    def remove_stopwords_from_tokens (self,lang=None,is_new=True):
        if lang is None:
            sw = set(stopwords.words("english"))
        else :
            sw = set(stopwords.words(lang))
        tks = [token for token in self.tokens if token not in sw]
        if is_new:
            self.tokens_without_stops = tks
        else :
            self.tokens = tks
        return self

    def stemme_tokens (self,stemmer=None,is_new=True):
        if stemmer is None:
            stemmer = PorterStemmer()
        xtr = [stemmer.stem(token) for token in self.tokens]
        if is_new :
            self.stem_tokens = xtr
        else :
            self.tokens = xtr
        return self

    def lematize_tokens (self,lematizer=None,is_new=True):
        if lematizer is None:
            lematizer = WordNetLemmatizer()
        xtr = [lematizer.lemmatize(token) for token in self.tokens]
        if is_new:
            self.lem_tokens = xtr
        else :
            self.tokens = xtr
        return self

    def replace_message_by_sorted_tokens(self,token_array=None):
        if token_array is None:
            token_array = self.tokens
        xtr = " ".join(sorted(token_array))
        self._message = xtr
        return self

[nltk_data] Downloading package wordnet to /home/alex/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [49]:

def apply_message_cleaner (text: str):
    return MessageCleaner()\
    .set_message(msg=text)\
    .remove_punctuation()\
    .remove_ru_special_sym()\
    .remove_ru_numbers()\
    .escape_single_symbol_words()\
    .to_lower()\
    .nltk_word_tokenize()\
    .lematize_tokens(is_new=False)\
    .remove_stopwords_from_tokens(lang="russian",is_new=False)\
    .replace_message_by_sorted_tokens()\
    .get_message()

apply_message_cleaner(text="Ну что сказать, я вижу кто-то наступил на грабли, Ты разочаровал меня, ты был натравлен.")

'вижу грабли наступил натравлен разочаровал сказать'

In [50]:
df_train['text'] = df_train['text'].apply(apply_message_cleaner)
df_val['text'] = df_val['text'].apply(apply_message_cleaner)
df_test['text'] = df_test['text'].apply(apply_message_cleaner)
df_train

id                                               text  class
0            0                         уезжаааааааай уезжала хочу      0
1            1  вотэтолюбовь девчата завтра кино любовь ребята...      1
2            2                            ненавидит пробки ретвит      0
3            3             запретный киевски котлету плод хочется      1
4            4                      боится босапопа есбоса мороза      1
...        ...                                                ...    ...
181462  181462                                 год классным новый      0
181463  181463      видишь игнорит привет сказать хочешь человека      0
181464  181464  аллергический ангины виде вкратце горла диагно...      0
181465  181465      достанется кнопочне кому серенький телефон ух      1
181466  181466  вандюх выложи навешаю нарядишь обязательно сде...      1

[181467 rows x 3 columns]

In [51]:
train_corpus = " ".join(df_train["text"])
train_corpus

'уезжаааааааай уезжала хочу вотэтолюбовь девчата завтра кино любовь ребята сегодня это ненавидит пробки ретвит запретный киевски котлету плод хочется боится босапопа есбоса мороза дома играет манчестер час девч жабу нкам остался писал правда пришол сч транспорт транспорт эт гладит мальчик маньяк момент ражик руке феликса неудачик поцарапал просто телефоне экран день запомнился надолго хахаа красава сомневался тебе вки глазах дней дорожают мартовские назад пару пут вообще месяц прошлый больной друзья извращено лучшие отвечу привет приду самые фантазией новое придумай бесплатное карте лимита оставить пополнение сделать увеличения завтра иду лах тожи болеть голова пойду померию прекращает температурку друзья знаю крайне кузов культурнейшие незнакомым ой оцинкован пиздите пожалуйста разговор человеком встряхиванием отмена работает австрия буду ждеееет паковать последние сегодня уладили формальности чемодан одноклассник плакала понимаю психанул сразу ставила это кого парни поймут те оуу про

In [52]:
train_corpus= MessageCleaner()\
             .set_message(msg=train_corpus)\
             .nltk_word_tokenize()\
             .tokens


from nltk.probability import FreqDist
dist = FreqDist(train_corpus)
tokens_filtered_top = [pair[0] for pair in dist.most_common(max_words-1)]

In [53]:
tokens_filtered_top[:30]

['это',
 'сегодня',
 'очень',
 'хочу',
 'день',
 'просто',
 'тебе',
 'завтра',
 'вообще',
 'вс',
 'спасибо',
 'буду',
 'почему',
 'могу',
 'блин',
 'люблю',
 'знаю',
 'всем',
 'дома',
 'год',
 'спать',
 'ещ',
 'время',
 'новый',
 'делать',
 'пока',
 'хочется',
 'такое',
 'такая',
 'такие']

In [55]:
vocabulary = {v: k for k, v in dict(enumerate(tokens_filtered_top, 1)).items()}
vocabulary

{'это': 1,
 'сегодня': 2,
 'очень': 3,
 'хочу': 4,
 'день': 5,
 'просто': 6,
 'тебе': 7,
 'завтра': 8,
 'вообще': 9,
 'вс': 10,
 'спасибо': 11,
 'буду': 12,
 'почему': 13,
 'могу': 14,
 'блин': 15,
 'люблю': 16,
 'знаю': 17,
 'всем': 18,
 'дома': 19,
 'год': 20,
 'спать': 21,
 'ещ': 22,
 'время': 23,
 'новый': 24,
 'делать': 25,
 'пока': 26,
 'хочется': 27,
 'такое': 28,
 'такая': 29,
 'такие': 30,
 'настроение': 31,
 'скоро': 32,
 'вчера': 33,
 'нужно': 34,
 'плохо': 35,
 'нам': 36,
 'дня': 37,
 'мои': 38,
 'хотя': 39,
 'мама': 40,
 'жизнь': 41,
 'утро': 42,
 'ахах': 43,
 'домой': 44,
 'люди': 45,
 'никто': 46,
 'жаль': 47,
 'кого': 48,
 'бля': 49,
 'нг': 50,
 'весь': 51,
 'жизни': 52,
 'года': 53,
 'равно': 54,
 'сижу': 55,
 'утра': 56,
 'думаю': 57,
 'ахаха': 58,
 'правда': 59,
 'вроде': 60,
 'школу': 61,
 'мной': 62,
 'надеюсь': 63,
 'одна': 64,
 'человек': 65,
 'кажется': 66,
 'нравится': 67,
 'болит': 68,
 'смотреть': 69,
 'привет': 70,
 'круто': 71,
 'таки': 72,
 'скучаю': 73,
 

In [58]:
import numpy as np

def text_to_sequence(text, maxlen):
    result = []
    tokens = word_tokenize(text.lower())
    tokens_filtered = [word for word in tokens if word.isalnum()]
    for word in tokens_filtered:
        if word in vocabulary:
            result.append(vocabulary[word])
    padding = [0]*(maxlen-len(result))
    return padding + result[-maxlen:]

In [59]:
x_train = np.asarray([text_to_sequence(text, max_len) for text in df_train["text"]], dtype=np.int32)
x_test = np.asarray([text_to_sequence(text, max_len) for text in df_test["text"]], dtype=np.int32)
x_val = np.asarray([text_to_sequence(text, max_len) for text in df_val["text"]], dtype=np.int32)

In [60]:
x_train[1]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 8, 2, 1], dtype=int32)

In [61]:
x_train.shape

(181467, 40)

In [62]:
num_classes = 2
y_train = keras.utils.to_categorical(df_train["class"], num_classes)
y_val = keras.utils.to_categorical(df_val["class"], num_classes)

In [64]:
import numpy as np
import keras
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Activation, Input, Embedding, Conv1D, GlobalMaxPool1D
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.callbacks import TensorBoard 
#tf.keras.metrics.categorical_crossentropy
#from keras.objectives import categorical_crossentropy
from keras.callbacks import EarlyStopping 

model = Sequential()
model.add(Embedding(input_dim=max_words, output_dim=128, input_length=max_len))
model.add(Conv1D(128, 3))
model.add(Activation("relu"))
model.add(GlobalMaxPool1D())
model.add(Dense(10))
model.add(Activation("relu"))
model.add(Dense(num_classes))
model.add(Activation('softmax'))

model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])


tensorboard=TensorBoard(log_dir='./logs', write_graph=True, write_images=True)
early_stopping=EarlyStopping(monitor='val_loss')  


2024-01-01 19:50:21.070607: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:894] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-01-01 19:50:22.157073: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2211] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [65]:
history = model.fit(x_train, y_train,
                    batch_size=batch_size,
                    epochs=epochs,
                    verbose=1,
                    validation_split=0.1,
                    callbacks=[tensorboard, early_stopping])


Epoch 1/20
319/319 [==============================] - 5s 13ms/step - loss: 0.6455 - accuracy: 0.6081 - val_loss: 0.6349 - val_accuracy: 0.6167
Epoch 2/20
319/319 [==============================] - 4s 13ms/step - loss: 0.6366 - accuracy: 0.6167 - val_loss: 0.6323 - val_accuracy: 0.6185
Epoch 3/20
319/319 [==============================] - 4s 13ms/step - loss: 0.6340 - accuracy: 0.6195 - val_loss: 0.6326 - val_accuracy: 0.6173


In [66]:
score = model.evaluate(x_val, y_val, batch_size=batch_size, verbose=1)
print('\n')
print('Test score:', score[0])
print('Test accuracy:', score[1])

45/45 [==============================] - 0s 4ms/step - loss: 0.6389 - accuracy: 0.6157


Test score: 0.6389111876487732
Test accuracy: 0.6157474517822266


In [7]:
train_corpus = " ".join(df_train["text"])
train_corpus = train_corpus.lower()

In [ ]:
train_corpus = " ".join(df_train["text"])
train_corpus = train_corpus.lower()

In [ ]:
df_train['text'] = df_train['text'].apply(preprocess_text)
df_val['text'] = df_val['text'].apply(preprocess_text)
df_test['text'] = df_test['text'].apply(preprocess_text)